In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.window import Window

In [0]:
# Define the path to the Delta table in the bronze layer
silver_table_path = "amazon.streamdb.streaming_cleaned"

# Read the streaming data from the Delta table
streaming_silver_df = spark.readStream \
    .table(silver_table_path)

In [0]:
streaming_silver_df.display()

timestamp user_id event_type device_type session_id EventProcessedUtcTime PartitionId EventEnqueuedUtcTime product_id category sub_category price search_term product_id_cart_contents quantity_cart_contents price_cart_contents 1.7234295201133268E9 CUST-14631 Add to Cart Mobile S959-4745249960 2024-08-12T02:25:20.763695Z 0 2024-08-12T02:25:20.639Z WW-561417 Women'S Clothing western wear null null null null null 1.7234295209070451E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:21.561912Z 0 2024-08-12T02:25:21.514Z F-221971 home & kitchen Furniture null null null null null 1.7234295209729657E9 CUST-13727 Search Desktop S806-7767844990 2024-08-12T02:25:21.562041Z 0 2024-08-12T02:25:21.529Z null Accessories null null handbags & clutches null null null 1.7234295221478453E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:22.873224Z 0 2024-08-12T02:25:22.67Z null accessories null null null null null null 1.7234295240960817E9 CUST-08853 Browse Product Desktop S594-7571885355 2024-08-12T02:25:25.07663Z 0 2024-08-12T02:25:24.904Z CS-117376 men's shoes Casual Shoes null null null null null 1.7234295245287743E9 CUST-17226 Add to Cart Desktop S647-5737266877 2024-08-12T02:25:25.5142Z 0 2024-08-12T02:25:25.31Z F-221971 Home & Kitchen furniture null null null null null 1.7234295248170295E9 CUST-16063 AppLogin Mobile S485-7090286144 2024-08-12T02:25:25.51439Z 0 2024-08-12T02:25:25.389Z null null null null null null null null 1.7234295245831337E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:25.514655Z 0 2024-08-12T02:25:25.404Z PCA-426149 beauty & health Personal Care Appliances null null null null null 1.7234295256875393E9 CUST-11875 Apply Filter Mobile S128-5985264117 2024-08-12T02:25:26.404585Z 0 2024-08-12T02:25:26.232Z null accessories null null null null null null 1.7234295293363063E9 CUST-17226 Browse Product Desktop S647-5737266877 2024-08-12T02:25:30.014005Z 0 2024-08-12T02:25:29.842Z J-335697 men's clothing Jeans null null null null null 1.723429529922018E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:30.780263Z 0 2024-08-12T02:25:30.654Z null Women'S Clothing null null ethnic wear null null null 1.723429530246815E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:31.107853Z 0 2024-08-12T02:25:30.92Z null Appliances null null all appliances null null null 1.7234295304006813E9 CUST-16063 Browse Product Mobile S485-7090286144 2024-08-12T02:25:31.108233Z 0 2024-08-12T02:25:31.029Z WW-575375 women's clothing Western Wear null null null null null 1.723429530499204E9 CUST-13727 Browse Product Desktop S806-7767844990 2024-08-12T02:25:31.108347Z 0 2024-08-12T02:25:31.045Z MF-415214 stores Men's Fashion null null null null null 1.7234295336797323E9 CUST-08853 Search Desktop S594-7571885355 2024-08-12T02:25:34.639063Z 0 2024-08-12T02:25:34.483Z null Women'S Clothing null null western wear null null null 1.7234295339805431E9 CUST-15987 Browse Product Desktop S352-3276363757 2024-08-12T02:25:34.857744Z 0 2024-08-12T02:25:34.67Z AE-046994 tv, audio & cameras All Electronics null null null null null 1.7234295341288753E9 CUST-07528 Apply Filter Desktop S308-9517299393 2024-08-12T02:25:34.857929Z 0 2024-08-12T02:25:34.67Z null accessories null null null null null null 1.7234295350993273E9 CUST-11078 Apply Filter Desktop S526-7423099512 2024-08-12T02:25:35.842016Z 0 2024-08-12T02:25:35.608Z null home & kitchen null null null null null null 1.7234295359345906E9 CUST-11875 Search Mobile S128-5985264117 2024-08-12T02:25:36.607621Z 0 2024-08-12T02:25:36.451Z null Tv, Audio & Cameras null null speakers null null null 1.723429537685823E9 CUST-15987 Add to Cart Desktop S352-3276363757 2024-08-12T02:25:38.373376Z 0 2024-08-12T02:25:38.233Z AE-046994 Tv, Audio & Cameras all electronics null null null null null 1.7234295377236638E9 CUST-07528 Browse Product Desktop S308-9517299393 2024-08-12T02:25:38.373563Z 0 2024-08-12T02:25:38.248Z R-430386 bags & luggage Rucksacks null null nu

#### Joins with Watermarking & Window

In [0]:
# Step 1: Apply watermarking and aggregate total clicks on user level
interaction_df_01 = streaming_silver_df \
    .withWatermark("EventProcessedUtcTime", "10 minutes") \
    .groupBy(
        col("user_id"),
        window(col("EventProcessedUtcTime"), "5 minutes")
    ) \
    .agg(
        count("*").alias("total_clicks")
    )

In [0]:
interaction_df_01.display()

user_id window total_clicks CUST-05103 List(2024-08-08T17:30:00Z, 2024-08-08T17:35:00Z) 13 CUST-17296 List(2024-08-08T18:35:00Z, 2024-08-08T18:40:00Z) 16 CUST-17542 List(2024-08-09T02:10:00Z, 2024-08-09T02:15:00Z) 9 CUST-04535 List(2024-08-08T22:35:00Z, 2024-08-08T22:40:00Z) 11 CUST-05756 List(2024-08-10T19:05:00Z, 2024-08-10T19:10:00Z) 7 CUST-09437 List(2024-08-13T00:45:00Z, 2024-08-13T00:50:00Z) 11 CUST-08046 List(2024-08-11T20:45:00Z, 2024-08-11T20:50:00Z) 14 CUST-16589 List(2024-08-13T22:10:00Z, 2024-08-13T22:15:00Z) 20 CUST-11130 List(2024-08-12T08:50:00Z, 2024-08-12T08:55:00Z) 11 CUST-03824 List(2024-08-08T22:10:00Z, 2024-08-08T22:15:00Z) 16 CUST-18863 List(2024-08-08T18:15:00Z, 2024-08-08T18:20:00Z) 2 CUST-16418 List(2024-08-11T01:10:00Z, 2024-08-11T01:15:00Z) 3 CUST-05592 List(2024-08-11T19:40:00Z, 2024-08-11T19:45:00Z) 12 CUST-05681 List(2024-08-12T23:55:00Z, 2024-08-13T00:00:00Z) 7 CUST-15424 List(2024-08-11T20:15:00Z, 2024-08-11T20:20:00Z) 1 CUST-03876 List(2024-08-10T08:40:00Z, 2024-08-10T08:45:00Z) 3 CUST-15403 List(2024-08-09T05:10:00Z, 2024-08-09T05:15:00Z) 3 CUST-19750 List(2024-08-10T20:00:00Z, 2024-08-10T20:05:00Z) 8 CUST-00126 List(2024-08-13T19:40:00Z, 2024-08-13T19:45:00Z) 6 CUST-19678 List(2024-08-09T03:00:00Z, 2024-08-09T03:05:00Z) 11 CUST-09893 List(2024-08-13T10:40:00Z, 2024-08-13T10:45:00Z) 1 CUST-00668 List(2024-08-08T08:20:00Z, 2024-08-08T08:25:00Z) 18 CUST-11772 List(2024-08-10T22:55:00Z, 2024-08-10T23:00:00Z) 8 CUST-19232 List(2024-08-09T09:00:00Z, 2024-08-09T09:05:00Z) 15 CUST-16645 List(2024-08-08T17:40:00Z, 2024-08-08T17:45:00Z) 7 CUST-10433 List(2024-08-13T20:20:00Z, 2024-08-13T20:25:00Z) 9 CUST-07573 List(2024-08-10T07:00:00Z, 2024-08-10T07:05:00Z) 14 CUST-02914 List(2024-08-12T19:40:00Z, 2024-08-12T19:45:00Z) 13 CUST-07213 List(2024-08-13T07:00:00Z, 2024-08-13T07:05:00Z) 2 CUST-17530 List(2024-08-12T22:15:00Z, 2024-08-12T22:20:00Z) 2 CUST-15684 List(2024-08-10T04:05:00Z, 2024-08-10T04:10:00Z) 19 CUST-05963 List(2024-08-11T17:20:00Z, 2024-08-11T17:25:00Z) 7 CUST-16087 List(2024-08-09T09:50:00Z, 2024-08-09T09:55:00Z) 10 CUST-01408 List(2024-08-14T12:55:00Z, 2024-08-14T13:00:00Z) 20 CUST-12505 List(2024-08-10T13:25:00Z, 2024-08-10T13:30:00Z) 5 CUST-17991 List(2024-08-12T02:40:00Z, 2024-08-12T02:45:00Z) 14 CUST-03406 List(2024-08-10T19:00:00Z, 2024-08-10T19:05:00Z) 2 CUST-16558 List(2024-08-14T01:40:00Z, 2024-08-14T01:45:00Z) 10 CUST-08989 List(2024-08-13T08:00:00Z, 2024-08-13T08:05:00Z) 15 CUST-09054 List(2024-08-10T23:30:00Z, 2024-08-10T23:35:00Z) 2 CUST-06968 List(2024-08-10T21:45:00Z, 2024-08-10T21:50:00Z) 9 CUST-00066 List(2024-08-08T22:05:00Z, 2024-08-08T22:10:00Z) 7 CUST-13252 List(2024-08-10T11:45:00Z, 2024-08-10T11:50:00Z) 5 CUST-05048 List(2024-08-10T04:50:00Z, 2024-08-10T04:55:00Z) 12 CUST-17132 List(2024-08-13T11:00:00Z, 2024-08-13T11:05:00Z) 6 CUST-07031 List(2024-08-13T23:30:00Z, 2024-08-13T23:35:00Z) 19 CUST-00904 List(2024-08-09T15:20:00Z, 2024-08-09T15:25:00Z) 15 CUST-06626 List(2024-08-10T13:25:00Z, 2024-08-10T13:30:00Z) 3 CUST-13095 List(2024-08-11T22:40:00Z, 2024-08-11T22:45:00Z) 6 CUST-18205 List(2024-08-12T18:00:00Z, 2024-08-12T18:05:00Z) 5 CUST-12113 List(2024-08-09T19:30:00Z, 2024-08-09T19:35:00Z) 12 CUST-05787 List(2024-08-11T08:55:00Z, 2024-08-11T09:00:00Z) 17 CUST-07235 List(2024-08-09T20:30:00Z, 2024-08-09T20:35:00Z) 6 CUST-02523 List(2024-08-08T08:45:00Z, 2024-08-08T08:50:00Z) 2 CUST-08187 List(2024-08-12T17:25:00Z, 2024-08-12T17:30:00Z) 2 CUST-01030 List(2024-08-12T03:25:00Z, 2024-08-12T03:30:00Z) 4 CUST-10877 List(2024-08-13T06:10:00Z, 2024-08-13T06:15:00Z) 12 CUST-02857 List(2024-08-12T10:50:00Z, 2024-08-12T10:55:00Z) 5 CUST-09146 List(2024-08-09T09:30:00Z, 2024-08-09T09:35:00Z) 19 CUST-13388 List(2024-08-11T23:45:00Z, 2024-08-11T23:50:00Z) 11 CUST-12884 List(2024-08-10T11:50:00Z, 2024-08-10T11:55:00Z) 14 CUST-01210 List(2024-08-11T02:55:00Z, 2024-08-11T03:00:00Z) 14 CUST-04781 List(2024-08-11T04:15:00Z, 2024-08-11T04:20:00Z) 9 CUST-01174 List(2024-08-12T00:30:00Z

In [0]:
checkpoint_path_gold_clicks = "/mnt/amazonopcheckpoint/chekpointlocgoldclicks"

interaction_df_01.writeStream \
    .trigger(processingTime="60 seconds")\
    .outputMode("complete") \
    .option("checkpointLocation", checkpoint_path_gold_clicks) \
    .toTable("amazon.streamdb.total_clicks_gold_fact")

In [0]:
%sql
select * from amazon.streamdb.total_clicks_gold_fact;

user_id window total_clicks CUST-01832 List(2024-08-12T02:05:00Z, 2024-08-12T02:10:00Z) 9 CUST-01094 List(2024-08-10T11:05:00Z, 2024-08-10T11:10:00Z) 2 CUST-06022 List(2024-08-09T23:15:00Z, 2024-08-09T23:20:00Z) 16 CUST-12628 List(2024-08-09T09:15:00Z, 2024-08-09T09:20:00Z) 15 CUST-05881 List(2024-08-14T01:45:00Z, 2024-08-14T01:50:00Z) 6 CUST-11301 List(2024-08-12T07:20:00Z, 2024-08-12T07:25:00Z) 11 CUST-03409 List(2024-08-08T08:25:00Z, 2024-08-08T08:30:00Z) 5 CUST-09404 List(2024-08-10T22:35:00Z, 2024-08-10T22:40:00Z) 2 CUST-05972 List(2024-08-14T06:05:00Z, 2024-08-14T06:10:00Z) 16 CUST-16136 List(2024-08-09T03:05:00Z, 2024-08-09T03:10:00Z) 18 CUST-09845 List(2024-08-11T10:25:00Z, 2024-08-11T10:30:00Z) 13 CUST-03997 List(2024-08-11T03:25:00Z, 2024-08-11T03:30:00Z) 15 CUST-16490 List(2024-08-13T07:25:00Z, 2024-08-13T07:30:00Z) 13 CUST-02539 List(2024-08-12T10:35:00Z, 2024-08-12T10:40:00Z) 20 CUST-16693 List(2024-08-08T14:55:00Z, 2024-08-08T15:00:00Z) 21 CUST-10155 List(2024-08-14T04:45:00Z, 2024-08-14T04:50:00Z) 19 CUST-16702 List(2024-08-14T05:10:00Z, 2024-08-14T05:15:00Z) 4 CUST-19497 List(2024-08-14T12:00:00Z, 2024-08-14T12:05:00Z) 16 CUST-04590 List(2024-08-10T17:35:00Z, 2024-08-10T17:40:00Z) 12 CUST-02362 List(2024-08-13T17:50:00Z, 2024-08-13T17:55:00Z) 9 CUST-00574 List(2024-08-13T20:45:00Z, 2024-08-13T20:50:00Z) 19 CUST-18246 List(2024-08-13T12:15:00Z, 2024-08-13T12:20:00Z) 17 CUST-12499 List(2024-08-08T16:15:00Z, 2024-08-08T16:20:00Z) 2 CUST-01261 List(2024-08-14T09:40:00Z, 2024-08-14T09:45:00Z) 8 CUST-14720 List(2024-08-09T23:55:00Z, 2024-08-10T00:00:00Z) 2 CUST-04498 List(2024-08-13T18:25:00Z, 2024-08-13T18:30:00Z) 2 CUST-10864 List(2024-08-12T11:00:00Z, 2024-08-12T11:05:00Z) 3 CUST-14801 List(2024-08-13T11:15:00Z, 2024-08-13T11:20:00Z) 13 CUST-07594 List(2024-08-09T21:25:00Z, 2024-08-09T21:30:00Z) 11 CUST-17927 List(2024-08-09T06:35:00Z, 2024-08-09T06:40:00Z) 1 CUST-00320 List(2024-08-13T12:55:00Z, 2024-08-13T13:00:00Z) 20 CUST-07332 List(2024-08-11T05:05:00Z, 2024-08-11T05:10:00Z) 15 CUST-18463 List(2024-08-14T12:25:00Z, 2024-08-14T12:30:00Z) 7 CUST-11770 List(2024-08-08T12:35:00Z, 2024-08-08T12:40:00Z) 3 CUST-00303 List(2024-08-11T16:25:00Z, 2024-08-11T16:30:00Z) 15 CUST-15254 List(2024-08-10T06:40:00Z, 2024-08-10T06:45:00Z) 5 CUST-19689 List(2024-08-12T02:35:00Z, 2024-08-12T02:40:00Z) 4 CUST-15906 List(2024-08-13T12:45:00Z, 2024-08-13T12:50:00Z) 19 CUST-07643 List(2024-08-11T02:10:00Z, 2024-08-11T02:15:00Z) 13 CUST-04514 List(2024-08-14T14:35:00Z, 2024-08-14T14:40:00Z) 5 CUST-03964 List(2024-08-08T08:05:00Z, 2024-08-08T08:10:00Z) 16 CUST-16649 List(2024-08-13T23:50:00Z, 2024-08-13T23:55:00Z) 4 CUST-19761 List(2024-08-10T12:45:00Z, 2024-08-10T12:50:00Z) 22 CUST-18247 List(2024-08-13T07:35:00Z, 2024-08-13T07:40:00Z) 1 CUST-19895 List(2024-08-08T10:20:00Z, 2024-08-08T10:25:00Z) 15 CUST-12158 List(2024-08-10T20:55:00Z, 2024-08-10T21:00:00Z) 7 CUST-06417 List(2024-08-11T09:30:00Z, 2024-08-11T09:35:00Z) 4 CUST-14534 List(2024-08-12T14:00:00Z, 2024-08-12T14:05:00Z) 2 CUST-17098 List(2024-08-08T07:50:00Z, 2024-08-08T07:55:00Z) 14 CUST-00749 List(2024-08-08T19:05:00Z, 2024-08-08T19:10:00Z) 14 CUST-06261 List(2024-08-13T01:20:00Z, 2024-08-13T01:25:00Z) 2 CUST-15496 List(2024-08-08T18:30:00Z, 2024-08-08T18:35:00Z) 4 CUST-15384 List(2024-08-09T02:15:00Z, 2024-08-09T02:20:00Z) 4 CUST-05300 List(2024-08-10T01:00:00Z, 2024-08-10T01:05:00Z) 2 CUST-18737 List(2024-08-08T06:25:00Z, 2024-08-08T06:30:00Z) 7 CUST-06033 List(2024-08-12T13:20:00Z, 2024-08-12T13:25:00Z) 11 CUST-09323 List(2024-08-13T00:55:00Z, 2024-08-13T01:00:00Z) 9 CUST-00496 List(2024-08-08T16:55:00Z, 2024-08-08T17:00:00Z) 7 CUST-12507 List(2024-08-09T21:40:00Z, 2024-08-09T21:45:00Z) 6 CUST-11062 List(2024-08-12T15:00:00Z, 2024-08-12T15:05:00Z) 12 CUST-19317 List(2024-08-08T21:35:00Z, 2024-08-08T21:40:00Z) 4 CUST-04615 List(2024-08-14T08:35:00Z, 2024-08-14T08:40:00Z) 9 CUST-14444 List(2024-08-14T11:00:00Z, 2024-08-14T11:05:00Z) 4 CUST-14812 List(2024-08-13T17:40:00Z,

In [0]:
# Step 2: Apply watermarking and aggregate total cart value on user level
session_df_01 = streaming_silver_df \
    .withWatermark("EventProcessedUtcTime", "10 minutes") \
    .groupBy(
        col("user_id"),
        window(col("EventProcessedUtcTime"), "5 minutes")
    ) \
    .agg(
        count("session_id").alias("total_sessions")
    )

In [0]:
session_df_01.display()

user_id window total_sessions CUST-05103 List(2024-08-08T17:30:00Z, 2024-08-08T17:35:00Z) 13 CUST-17296 List(2024-08-08T18:35:00Z, 2024-08-08T18:40:00Z) 16 CUST-17542 List(2024-08-09T02:10:00Z, 2024-08-09T02:15:00Z) 9 CUST-04535 List(2024-08-08T22:35:00Z, 2024-08-08T22:40:00Z) 11 CUST-05756 List(2024-08-10T19:05:00Z, 2024-08-10T19:10:00Z) 7 CUST-09437 List(2024-08-13T00:45:00Z, 2024-08-13T00:50:00Z) 11 CUST-08046 List(2024-08-11T20:45:00Z, 2024-08-11T20:50:00Z) 14 CUST-16589 List(2024-08-13T22:10:00Z, 2024-08-13T22:15:00Z) 20 CUST-11130 List(2024-08-12T08:50:00Z, 2024-08-12T08:55:00Z) 11 CUST-03824 List(2024-08-08T22:10:00Z, 2024-08-08T22:15:00Z) 16 CUST-18863 List(2024-08-08T18:15:00Z, 2024-08-08T18:20:00Z) 2 CUST-16418 List(2024-08-11T01:10:00Z, 2024-08-11T01:15:00Z) 3 CUST-05592 List(2024-08-11T19:40:00Z, 2024-08-11T19:45:00Z) 12 CUST-05681 List(2024-08-12T23:55:00Z, 2024-08-13T00:00:00Z) 7 CUST-15424 List(2024-08-11T20:15:00Z, 2024-08-11T20:20:00Z) 1 CUST-03876 List(2024-08-10T08:40:00Z, 2024-08-10T08:45:00Z) 3 CUST-15403 List(2024-08-09T05:10:00Z, 2024-08-09T05:15:00Z) 3 CUST-19750 List(2024-08-10T20:00:00Z, 2024-08-10T20:05:00Z) 8 CUST-00126 List(2024-08-13T19:40:00Z, 2024-08-13T19:45:00Z) 6 CUST-19678 List(2024-08-09T03:00:00Z, 2024-08-09T03:05:00Z) 11 CUST-09893 List(2024-08-13T10:40:00Z, 2024-08-13T10:45:00Z) 1 CUST-00668 List(2024-08-08T08:20:00Z, 2024-08-08T08:25:00Z) 18 CUST-11772 List(2024-08-10T22:55:00Z, 2024-08-10T23:00:00Z) 8 CUST-19232 List(2024-08-09T09:00:00Z, 2024-08-09T09:05:00Z) 15 CUST-16645 List(2024-08-08T17:40:00Z, 2024-08-08T17:45:00Z) 7 CUST-10433 List(2024-08-13T20:20:00Z, 2024-08-13T20:25:00Z) 9 CUST-07573 List(2024-08-10T07:00:00Z, 2024-08-10T07:05:00Z) 14 CUST-02914 List(2024-08-12T19:40:00Z, 2024-08-12T19:45:00Z) 13 CUST-07213 List(2024-08-13T07:00:00Z, 2024-08-13T07:05:00Z) 2 CUST-17530 List(2024-08-12T22:15:00Z, 2024-08-12T22:20:00Z) 2 CUST-15684 List(2024-08-10T04:05:00Z, 2024-08-10T04:10:00Z) 19 CUST-05963 List(2024-08-11T17:20:00Z, 2024-08-11T17:25:00Z) 7 CUST-16087 List(2024-08-09T09:50:00Z, 2024-08-09T09:55:00Z) 10 CUST-01408 List(2024-08-14T12:55:00Z, 2024-08-14T13:00:00Z) 20 CUST-12505 List(2024-08-10T13:25:00Z, 2024-08-10T13:30:00Z) 5 CUST-17991 List(2024-08-12T02:40:00Z, 2024-08-12T02:45:00Z) 14 CUST-03406 List(2024-08-10T19:00:00Z, 2024-08-10T19:05:00Z) 2 CUST-16558 List(2024-08-14T01:40:00Z, 2024-08-14T01:45:00Z) 10 CUST-08989 List(2024-08-13T08:00:00Z, 2024-08-13T08:05:00Z) 15 CUST-09054 List(2024-08-10T23:30:00Z, 2024-08-10T23:35:00Z) 2 CUST-06968 List(2024-08-10T21:45:00Z, 2024-08-10T21:50:00Z) 9 CUST-00066 List(2024-08-08T22:05:00Z, 2024-08-08T22:10:00Z) 7 CUST-13252 List(2024-08-10T11:45:00Z, 2024-08-10T11:50:00Z) 5 CUST-05048 List(2024-08-10T04:50:00Z, 2024-08-10T04:55:00Z) 12 CUST-17132 List(2024-08-13T11:00:00Z, 2024-08-13T11:05:00Z) 6 CUST-07031 List(2024-08-13T23:30:00Z, 2024-08-13T23:35:00Z) 19 CUST-00904 List(2024-08-09T15:20:00Z, 2024-08-09T15:25:00Z) 15 CUST-06626 List(2024-08-10T13:25:00Z, 2024-08-10T13:30:00Z) 3 CUST-13095 List(2024-08-11T22:40:00Z, 2024-08-11T22:45:00Z) 6 CUST-18205 List(2024-08-12T18:00:00Z, 2024-08-12T18:05:00Z) 5 CUST-12113 List(2024-08-09T19:30:00Z, 2024-08-09T19:35:00Z) 12 CUST-05787 List(2024-08-11T08:55:00Z, 2024-08-11T09:00:00Z) 17 CUST-07235 List(2024-08-09T20:30:00Z, 2024-08-09T20:35:00Z) 6 CUST-02523 List(2024-08-08T08:45:00Z, 2024-08-08T08:50:00Z) 2 CUST-08187 List(2024-08-12T17:25:00Z, 2024-08-12T17:30:00Z) 2 CUST-01030 List(2024-08-12T03:25:00Z, 2024-08-12T03:30:00Z) 4 CUST-10877 List(2024-08-13T06:10:00Z, 2024-08-13T06:15:00Z) 12 CUST-02857 List(2024-08-12T10:50:00Z, 2024-08-12T10:55:00Z) 5 CUST-09146 List(2024-08-09T09:30:00Z, 2024-08-09T09:35:00Z) 19 CUST-13388 List(2024-08-11T23:45:00Z, 2024-08-11T23:50:00Z) 11 CUST-12884 List(2024-08-10T11:50:00Z, 2024-08-10T11:55:00Z) 14 CUST-01210 List(2024-08-11T02:55:00Z, 2024-08-11T03:00:00Z) 14 CUST-04781 List(2024-08-11T04:15:00Z, 2024-08-11T04:20:00Z) 9 CUST-01174 List(2024-08-12T00:30:0

In [0]:
checkpoint_path_gold_sessions = "/mnt/amazonopcheckpoint/chekpointlocgoldsessions"

session_df_01.writeStream \
    .trigger(processingTime="60 seconds")\
    .outputMode("complete") \
    .option("checkpointLocation", checkpoint_path_gold_sessions) \
    .toTable("amazon.streamdb.total_sessions_gold_fact")

In [0]:
%sql
select * from amazon.streamdb.total_sessions_gold_fact;

user_id window total_sessions CUST-01832 List(2024-08-12T02:05:00Z, 2024-08-12T02:10:00Z) 9 CUST-01094 List(2024-08-10T11:05:00Z, 2024-08-10T11:10:00Z) 2 CUST-06022 List(2024-08-09T23:15:00Z, 2024-08-09T23:20:00Z) 16 CUST-12628 List(2024-08-09T09:15:00Z, 2024-08-09T09:20:00Z) 15 CUST-05881 List(2024-08-14T01:45:00Z, 2024-08-14T01:50:00Z) 6 CUST-11301 List(2024-08-12T07:20:00Z, 2024-08-12T07:25:00Z) 11 CUST-03409 List(2024-08-08T08:25:00Z, 2024-08-08T08:30:00Z) 5 CUST-09404 List(2024-08-10T22:35:00Z, 2024-08-10T22:40:00Z) 2 CUST-05972 List(2024-08-14T06:05:00Z, 2024-08-14T06:10:00Z) 16 CUST-16136 List(2024-08-09T03:05:00Z, 2024-08-09T03:10:00Z) 18 CUST-09845 List(2024-08-11T10:25:00Z, 2024-08-11T10:30:00Z) 13 CUST-03997 List(2024-08-11T03:25:00Z, 2024-08-11T03:30:00Z) 15 CUST-16490 List(2024-08-13T07:25:00Z, 2024-08-13T07:30:00Z) 13 CUST-02539 List(2024-08-12T10:35:00Z, 2024-08-12T10:40:00Z) 20 CUST-16693 List(2024-08-08T14:55:00Z, 2024-08-08T15:00:00Z) 21 CUST-10155 List(2024-08-14T04:45:00Z, 2024-08-14T04:50:00Z) 19 CUST-16702 List(2024-08-14T05:10:00Z, 2024-08-14T05:15:00Z) 4 CUST-19497 List(2024-08-14T12:00:00Z, 2024-08-14T12:05:00Z) 16 CUST-04590 List(2024-08-10T17:35:00Z, 2024-08-10T17:40:00Z) 12 CUST-02362 List(2024-08-13T17:50:00Z, 2024-08-13T17:55:00Z) 9 CUST-00574 List(2024-08-13T20:45:00Z, 2024-08-13T20:50:00Z) 19 CUST-18246 List(2024-08-13T12:15:00Z, 2024-08-13T12:20:00Z) 17 CUST-12499 List(2024-08-08T16:15:00Z, 2024-08-08T16:20:00Z) 2 CUST-01261 List(2024-08-14T09:40:00Z, 2024-08-14T09:45:00Z) 8 CUST-14720 List(2024-08-09T23:55:00Z, 2024-08-10T00:00:00Z) 2 CUST-04498 List(2024-08-13T18:25:00Z, 2024-08-13T18:30:00Z) 2 CUST-10864 List(2024-08-12T11:00:00Z, 2024-08-12T11:05:00Z) 3 CUST-14801 List(2024-08-13T11:15:00Z, 2024-08-13T11:20:00Z) 13 CUST-07594 List(2024-08-09T21:25:00Z, 2024-08-09T21:30:00Z) 11 CUST-17927 List(2024-08-09T06:35:00Z, 2024-08-09T06:40:00Z) 1 CUST-00320 List(2024-08-13T12:55:00Z, 2024-08-13T13:00:00Z) 20 CUST-07332 List(2024-08-11T05:05:00Z, 2024-08-11T05:10:00Z) 15 CUST-18463 List(2024-08-14T12:25:00Z, 2024-08-14T12:30:00Z) 7 CUST-11770 List(2024-08-08T12:35:00Z, 2024-08-08T12:40:00Z) 3 CUST-00303 List(2024-08-11T16:25:00Z, 2024-08-11T16:30:00Z) 15 CUST-15254 List(2024-08-10T06:40:00Z, 2024-08-10T06:45:00Z) 5 CUST-19689 List(2024-08-12T02:35:00Z, 2024-08-12T02:40:00Z) 4 CUST-15906 List(2024-08-13T12:45:00Z, 2024-08-13T12:50:00Z) 19 CUST-07643 List(2024-08-11T02:10:00Z, 2024-08-11T02:15:00Z) 13 CUST-04514 List(2024-08-14T14:35:00Z, 2024-08-14T14:40:00Z) 5 CUST-03964 List(2024-08-08T08:05:00Z, 2024-08-08T08:10:00Z) 16 CUST-16649 List(2024-08-13T23:50:00Z, 2024-08-13T23:55:00Z) 4 CUST-19761 List(2024-08-10T12:45:00Z, 2024-08-10T12:50:00Z) 22 CUST-18247 List(2024-08-13T07:35:00Z, 2024-08-13T07:40:00Z) 1 CUST-19895 List(2024-08-08T10:20:00Z, 2024-08-08T10:25:00Z) 15 CUST-12158 List(2024-08-10T20:55:00Z, 2024-08-10T21:00:00Z) 7 CUST-06417 List(2024-08-11T09:30:00Z, 2024-08-11T09:35:00Z) 4 CUST-14534 List(2024-08-12T14:00:00Z, 2024-08-12T14:05:00Z) 2 CUST-17098 List(2024-08-08T07:50:00Z, 2024-08-08T07:55:00Z) 14 CUST-00749 List(2024-08-08T19:05:00Z, 2024-08-08T19:10:00Z) 14 CUST-06261 List(2024-08-13T01:20:00Z, 2024-08-13T01:25:00Z) 2 CUST-15496 List(2024-08-08T18:30:00Z, 2024-08-08T18:35:00Z) 4 CUST-15384 List(2024-08-09T02:15:00Z, 2024-08-09T02:20:00Z) 4 CUST-05300 List(2024-08-10T01:00:00Z, 2024-08-10T01:05:00Z) 2 CUST-18737 List(2024-08-08T06:25:00Z, 2024-08-08T06:30:00Z) 7 CUST-06033 List(2024-08-12T13:20:00Z, 2024-08-12T13:25:00Z) 11 CUST-09323 List(2024-08-13T00:55:00Z, 2024-08-13T01:00:00Z) 9 CUST-00496 List(2024-08-08T16:55:00Z, 2024-08-08T17:00:00Z) 7 CUST-12507 List(2024-08-09T21:40:00Z, 2024-08-09T21:45:00Z) 6 CUST-11062 List(2024-08-12T15:00:00Z, 2024-08-12T15:05:00Z) 12 CUST-19317 List(2024-08-08T21:35:00Z, 2024-08-08T21:40:00Z) 4 CUST-04615 List(2024-08-14T08:35:00Z, 2024-08-14T08:40:00Z) 9 CUST-14444 List(2024-08-14T11:00:00Z, 2024-08-14T11:05:00Z) 4 CUST-14812 List(2024-08-13T17:40:00

#### Experiments - foreachBatch

In [0]:
checkpoint_path_gold_03 = "/mnt/amazonopcheckpoint/chekpointlocgoldtest03"

In [0]:
# Define the upsert function
def upsertToDelta(microBatchOutputDF, batchId):
    # Create a temporary view for the current micro-batch
    microBatchOutputDF.createOrReplaceTempView("updates")

    # Perform the MERGE operation
    microBatchOutputDF.sparkSession.sql(f"""
        MERGE INTO {delta_table} t
        USING updates s
        ON s.user_id = t.user_id AND s.window = t.window
        WHEN MATCHED THEN UPDATE SET *
        WHEN NOT MATCHED THEN INSERT *
    """)

In [0]:
delta_table = "amazon.streamdb.user_session_aggregates_gold_joins"

In [0]:
# Write the result to Delta with upsert logic
final_df.writeStream \
    .foreachBatch(upsertToDelta) \
    .outputMode("update") \
    .option("checkpointLocation", checkpoint_path_gold_03) \
    .start()

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-3782660352236498>, line 6
      1 # Write the result to Delta with upsert logic
      2 final_df.writeStream \
      3     .foreachBatch(upsertToDelta) \
      4     .outputMode("update") \
      5     .option("checkpointLocation", checkpoint_path_gold_03) \
----> 6     .start()

File /databricks/spark/python/pyspark/sql/streaming/readwriter.py:1464, in DataStreamWriter.start(self, path, format, outputMode, partitionBy, queryName, **options)
   1462     self.queryName(queryName)
   1463 if path is None:
-> 1464     return self._sq(self._jwrite.start())
   1465 else:
   1466     return self._sq(self._jwrite.start(path))

File /databricks/spark/python/lib/py4j-0.10.9.7-src.zip/py4j/java_gateway.py:1355, in JavaMember.__call__(self, *args)
   1349 command = proto.CALL_COMMAND_NAME +\
   1350     self.command_header +\
   1351

In [0]:
# Write the result to Delta with upsert logic
final_df.writeStream \
    .foreachBatch(upsertToDelta) \
    .outputMode("append") \
    .option("checkpointLocation", checkpoint_path_gold_03) \
    .start()

In [0]:
# Write the result to Delta with upsert logic
final_df.writeStream \
    .foreachBatch(upsertToDelta) \
    .outputMode("append") \
    .option("checkpointLocation", checkpoint_path_gold_03) \
    .start()